# Differentiating with the LEAN algorithm
This example shows how to differentiate cycler data using the LEAN algorithm developed by 

First import the package and dataset:

In [1]:
import pyprobe
import numpy as np
info_dictionary = {'Name': 'Sample cell',
                   'Chemistry': 'NMC622',
                   'Nominal Capacity [Ah]': 0.04,
                   'Cycler number': 1,
                   'Channel number': 1,}
data_directory = '../tests/sample_data/neware'

# Create a cell object
cell = pyprobe.Cell(info_dictionary)
cell.add_procedure(procedure_name='Sample',
                   folder_path = data_directory,
                   filename = 'sample_data_neware.parquet')

The break-in cycles of this dataset are at C/10, so can be analysed as pseudo-OCV curves. We're going to look at the last cycle:

In [2]:
final_cycle = cell.procedure['Sample'].experiment('Break-in Cycles').cycle(-1)
fig = pyprobe.Plot()
fig.add_line(final_cycle, 'Time [hr]', 'Voltage [V]')
fig.show()

In [3]:
discharge_dQdV = pyprobe.methods.differentiation.gradient(method ='LEAN',
                                                          input_data = final_cycle.discharge(0),
                                                            x ='Capacity [Ah]',
                                                            y ='Voltage [V]',
                                                            k = 10,
                                                            gradient = 'dxdy'
                                                    )
charge_dQdV = pyprobe.methods.differentiation.gradient(method ='LEAN',
                                                          input_data = final_cycle.charge(0),
                                                            x ='Capacity [Ah]',
                                                            y ='Voltage [V]',
                                                            k = 10,
                                                            gradient = 'dxdy',
                                                            section = 'longest'
                                                    )
fig = pyprobe.Plot()
fig.add_line(discharge_dQdV, 'Capacity [Ah]', 'd(Capacity [Ah])/d(Voltage [V])')
fig.add_line(charge_dQdV, 'Capacity [Ah]', 'd(Capacity [Ah])/d(Voltage [V])', color='red')
fig.show()

On-the-fly unit conversion allows this to be computed in whichever unit you choose:

In [4]:
discharge_dQdV = pyprobe.methods.differentiation.gradient(method ='LEAN',
                                                          input_data = final_cycle.discharge(0),
                                                            x ='Capacity [mAh]',
                                                            y ='Voltage [V]',
                                                            k = 10,
                                                            gradient = 'dxdy'
                                                    )
charge_dQdV = pyprobe.methods.differentiation.gradient(method ='LEAN',
                                                          input_data = final_cycle.charge(0),
                                                            x ='Capacity [mAh]',
                                                            y ='Voltage [V]',
                                                            k = 10,
                                                            gradient = 'dxdy',
                                                    )
fig = pyprobe.Plot()
fig.add_line(discharge_dQdV, 'Capacity [mAh]', 'd(Capacity [mAh])/d(Voltage [V])')
fig.add_line(charge_dQdV, 'Capacity [mAh]', 'd(Capacity [mAh])/d(Voltage [V])', color='red')
fig.show()

To align the curves, we can instead plot `Cycle Capacity [Ah]` which is set to zero at the beginning of the filtered cycle.

In [6]:
discharge_dQdV = pyprobe.methods.differentiation.gradient(method ='LEAN',
                                                          input_data = final_cycle.discharge(0),
                                                            x ='Cycle Capacity [Ah]',
                                                            y ='Voltage [V]',
                                                            k = 10,
                                                            gradient = 'dxdy'
                                                    )
charge_dQdV = pyprobe.methods.differentiation.gradient(method ='LEAN',
                                                          input_data = final_cycle.charge(0),
                                                            x ='Cycle Capacity [Ah]',
                                                            y ='Voltage [V]',
                                                            k = 10,
                                                            gradient = 'dxdy',
                                                    )
fig = pyprobe.Plot()
fig.add_line(discharge_dQdV, 'Cycle Capacity [Ah]', 'd(Cycle Capacity [Ah])/d(Voltage [V])', color='red', label='Discharge')
fig.add_line(charge_dQdV, 'Cycle Capacity [Ah]', 'd(Cycle Capacity [Ah])/d(Voltage [V])', color='blue', label='Charge')
fig.show()

The LEAN method is only applicable when the `x` data is uniformly spaced. The example above uses the default method behaviour of differentiating only the longest uniformly spaced period. If your `x` data has multiple uniformly spaced periods, however, you can use this method with the `section = 'all'` option.

The pulse below has two sampling periods:

In [43]:
pulse_rest = cell.procedure['Sample'].experiment('Discharge Pulses').rest(7,8)
print('dt = ', np.diff(pulse_rest('Time [s]')))

fig = pyprobe.Plot()
fig.add_line(pulse_rest, 'Time [s]', 'Voltage [V]')
fig.show()

dt =  [0.1 0.1 0.1 ... 1.  1.  1. ]


In [44]:
rest_dVdt = pyprobe.methods.differentiation.gradient(method ='LEAN',
                                                        input_data = pulse_rest,
                                                        x ='Time [s]',
                                                        y ='Voltage [mV]',
                                                        k = 20,
                                                        gradient = 'dydx',
                                                        section = 'all'
                                                        )

fig = pyprobe.Plot()
fig.add_line(rest_dVdt, 'Time [s]', 'd(Voltage [mV])/d(Time [s])')
fig.show()